In [1]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FFMpegWriter
%matplotlib osx 

In [2]:
def display(A):
    maxX = A.shape[0]
    maxY = A.shape[1]
    B = np.zeros((maxY, maxX))
    for ix in range(0,maxX):
        for iy in range(0,maxY):
            B[maxY-1-iy,ix] = A[ix,iy]
    
    plt.rcParams['figure.figsize'] = [6, 6/maxX*maxY]
    plt.imshow(B, cmap = 'copper_r'); 
    plt.axis('off'); 
    plt.show()
    plt.draw()
    plt.pause(0.7)
    

In [3]:
metadata = dict(title='Bacteria Competition', artist='Kaylee Christensen',comment='Final Project')
writer = FFMpegWriter(fps=15, metadata=metadata)
fig = plt.figure()

In [4]:
#Initial Conditions
nParticles = 20000
maxX = 150
maxY = 100

#Set Up Bacteria 0
A = np.zeros((maxX, maxY))
A[:,0] = 1
yBuffer = 2
yStart  = 1 + yBuffer
comp = 0.40       #competition factor

#Set Up Bacteria 1
A[:,maxY-1] = 2
yBuffer1 = 2 
yStart1  = maxY - 1 - 1 - yBuffer1
comp1 = 1 - comp    #competition factor

with writer.saving(fig, "finalproject.mp4", dpi=200):
    for i in range(0,nParticles):

        #Movement for Bacteria 1
        # Compute new starting point on the line y=yStart
        x1  = np.random.randint(0,maxX)
        y1  = yStart1; 

        x  = np.random.randint(0,maxX)
        y  = yStart; #always start at upper limit

        while True:
            xOrg1 = x1
            yOrg1 = y1

            r1 = np.random.random(); # Random float:  0.0 <= r < 1.0
            #based on the value of 'r', move the particle
            #left, right, up, or down and change x and y accordingly
            if (0.0 <= r1 <= 0.25):
                x1 = x1 - 1
            elif (0.25 <= r1 <= 0.5):
                x1 = x1 + 1
            elif (0.5 <= r1 <= 0.75):
                y1 = y1 + 1
            elif (0.75 <= r1 <= 1.0):
                y1 = y1 - 1

                

            #now apply periodic boundary conditions to 'x'
            if (x1 < 0):
                x1 = maxX + x1
            if (x1 >= maxX):
                x1 = x1 - maxX          

            if (y1 < yStart1 or A[x1,y1] == 2): #or y>yStart
                x1 = xOrg1
                y1 = yOrg1
                continue; # if this site has been taken try moving in a different direction

            #determine the x coordionates of the left and right neighbors
            #store them in 'xm' and 'xp' and apply periodic boundary conditions again
            xp1 = x1 - 1
            xm1 = x1 + 1
            yp1 = y1 - 1
            ym1 = y1 + 1
            if (xp1 < 0):
                xp1 = maxX + xp1
            if (xp1 >= maxX):
                xp1 = xp1 - maxX
            if (xm1 < 0):
                xm1 = maxX + xm1
            if (xm1 >= maxX):
                xm1 = xm1 - maxX

            n1 = 0 #counting number of same neighbors
            d1 = 0 #counting number of different neighbors
            if (A[xp1,y1] == 2):
                n1 += 1
            if (A[xp1,y1] == 1):
                d1 += 1
            if (A[xm1,y1] == 2):
                n1 += 1
            if (A[xm1,y1] == 1):
                d1 += 1
            if (A[x1,yp1] == 2):
                n1 += 1
            if (A[x1,yp1] == 1):
                d1 += 1
            if (A[x1,ym1] == 2):
                n1 += 1
            if (A[x1,ym1] == 1):
                d1 += 1

            p = np.random.random()
            p1 = 0.1
            if (n1 == 1):
                p0 = p1
            if (n1 == 2):
                p0 = p1 * 10
            if (n1 == 3):
                p0 = p1 * 20
            if (n1 == 4):
                p0 = p1 * 30


            # Determine if any neighboring site is occupied
            # if that is the case, enter the following 'if' clause
            if (n1 > 0 and A[x1,y1] == 0):      
                if (p <= p0):
                    A[x1,y1] = 2
                    if (d1 > 0):
                        compr = np.random.random()
                        if (compr < comp):
                            A[x1,y1] = 1
                    if (y1-yBuffer1 < yStart1 and y1-yBuffer1 > 0 and A[x1,y1] == 2): 
                        yStart1 = y1-yBuffer1

                    if (i%1000==0): 
                        print(f'i= {i} \tx={x1} \ty={y1} \tyStart={yStart1}')

                    nNewParticlesPerFrame = 1000 
                    if (i%nNewParticlesPerFrame==0): 
                        display(A)
                        plt.show()
                        writer.grab_frame()

                    break # particle was attached, break out of current loop and insert next one
            elif (n1 > 0 and A[x1,y1] == 1):
                if (p <= p0):
                    compr = np.random.random()
                    if (compr <= comp1):
                        A[x1,y1] = 2
                        if (d1 > 0):
                            compr = np.random.random()
                            if (compr <= comp):
                                A[x1,y1] = 1
                        if (y1-yBuffer1 < yStart1 and y1-yBuffer1 > 0 and A[x1,y1] == 2): 
                            yStart1 = y1-yBuffer1

                        if (i%1000==0): 
                            print(f'i= {i} \tx={x1} \ty={y1} \tyStart={yStart1}')

                        nNewParticlesPerFrame = 1000 
                        if (i%nNewParticlesPerFrame==0): 
                            display(A)
                            plt.show()
                            writer.grab_frame()

                        break # particle was attached, break out of current loop and insert next one

        if (yStart1-1==0): 
            print(f'Structures reached bottom Y limit after only {i} particles')
            break


        while True:
            xOrg = x
            yOrg = y

            r = np.random.random(); # Random float:  0.0 <= r < 1.0
            #based on the value of 'r', move the particle
            #left, right, up, or down and change x and y accordingly
            if (0.0 <= r <= 0.25):
                x = x - 1
            if (0.25 <= r <= 0.5):
                x = x + 1
            if (0.5 <= r <= 0.75):
                y = y + 1
            if (0.75 <= r <= 1.0):
                y = y - 1

            #now apply periodic boundary conditions to 'x'
            if (x < 0):
                x = maxX + x
            if (x >= maxX):
                x = x - maxX

            if (A[x,y] == 1 or y>yStart): 
                x = xOrg
                y = yOrg
                continue; # if this site has been taken try moving in a different direction

            #determine the x coordionates of the left and right neighbors
            #store them in 'xm' and 'xp' and apply periodic boundary conditions again
            xp = x - 1
            xm = x + 1
            yp = y - 1
            ym = y + 1
            if (xp < 0):
                xp = maxX + xp
            if (xp >= maxX):
                xp = xp - maxX
            if (xm < 0):
                xm = maxX + xm
            if (xm >= maxX):
                xm = xm - maxX

            n = 0
            d = 0
            if (A[xp,y] == 1):
                n += 1
            if (A[xp,y] == 2):
                d += 1
            if (A[xm,y] == 1):
                n += 1
            if (A[xm,y] == 2):
                d += 1
            if (A[x,yp] == 1):
                n += 1
            if (A[x,yp] == 2):
                d += 1
            if (A[x,ym] == 1):
                n += 1
            if (A[x,ym] == 2):
                d += 1

            p = np.random.random()
            p1 = 0.1
            if (n == 1):
                p0 = p1
            if (n == 2):
                p0 = p1 * 10
            if (n == 3):
                p0 = p1 * 20
            if (n == 4):
                p0 = p1 * 30


            # Determine if any neighboring site is occupied
            # if that is the case, enter the following 'if' clause
            if (n > 0 and A[x,y] == 0): 
                if (p <= p0): 
                    A[x,y] = 1
                    if (d > 0):
                        compr = np.random.random()
                        if (compr < comp1):
                            A[x,y] = 2
                    if (y+yBuffer>yStart and y+yBuffer<maxY and A[x,y] == 1): 
                        yStart = y+yBuffer

                    if (i%1000==0): 
                        print(f'i= {i} \tx={x} \ty={y} \tyStart={yStart}')

                    nNewParticlesPerFrame = 1000 
                    if (i%nNewParticlesPerFrame==0): 
                        display(A)
                        plt.show()
                        writer.grab_frame()

                    break # particle was attached, break out of current loop and insert next one
            elif (n > 0 and A[x,y] == 2):
                if (p <= p0):
                    compr = np.random.random()
                    if (compr <= comp):
                        A[x,y] = 1
                        if (d > 0):
                            compr = np.random.random()
                            if (compr < comp1):
                                A[x,y] = 2
                        if (y+yBuffer>yStart and y+yBuffer<maxY and A[x,y] == 1): 
                            yStart = y+yBuffer

                        if (i%1000==0): 
                            print(f'i= {i} \tx={x} \ty={y} \tyStart={yStart}')

                        nNewParticlesPerFrame = 1000 
                        if (i%nNewParticlesPerFrame==0): 
                            display(A)
                            plt.show()
                            writer.grab_frame()

                        break # particle was attached, break out of current loop and insert next one

        if (yStart+1==maxY): 
            print(f'Structures reached top Y limit after only {i} particles')
            break

    display(A)
    plt.show()
    writer.grab_frame()

i= 0 	x=43 	y=98 	yStart=96
i= 0 	x=36 	y=1 	yStart=3
i= 1000 	x=8 	y=88 	yStart=78
i= 1000 	x=12 	y=12 	yStart=23
i= 2000 	x=80 	y=69 	yStart=55
i= 2000 	x=138 	y=27 	yStart=39
i= 3000 	x=24 	y=40 	yStart=37
i= 3000 	x=107 	y=45 	yStart=54
i= 4000 	x=41 	y=25 	yStart=21
i= 4000 	x=11 	y=58 	yStart=70
i= 5000 	x=42 	y=7 	yStart=5
i= 5000 	x=72 	y=80 	yStart=86
Structures reached bottom Y limit after only 5347 particles
